# Discovering Brown Dwarfs with Backyard Worlds!

In this notebook we'll explore a bit of the physics, astronomy and math behind how we can discover new nearby neighbors of the Sun referred to as [brown dwarfs](https://en.wikipedia.org/wiki/Brown_dwarf). Then we'll look through some telescope data to identify real brown dwarfs hidden among other stars, galaxies and detector noise.

Brown dwarfs are celestial objects with masses in between those of stars and those of giant planets like Jupiter. Below is an artist rendering of a brown dwarf. You can think of them like oversized versions of Jupiter, but floating around all alone in interstellar space.

<img src="https://upload.wikimedia.org/wikipedia/commons/thumb/e/e0/Artist%E2%80%99s_conception_of_a_brown_dwarf_like_2MASSJ22282889-431026.jpg/1920px-Artist%E2%80%99s_conception_of_a_brown_dwarf_like_2MASSJ22282889-431026.jpg" width="800">

You might wonder: why should we care about brown dwarfs? There are many different ways to answer this. The atmospheres of brown dwarfs are very similar to those of giant exoplanets, but can be characterized in detail without the glare of a much brighter host star interfering. These brown dwarf atmospheres show strong signatures of water and methane. Some brown dwarfs may in fact be rogue planets ejected from the star system in which they were originally born.

Because brown dwarfs are so dim, it still remains possible that there could be an as-yet overlooked brown dwarf closer to us than [Proxima Centauri](https://en.wikipedia.org/wiki/Proxima_Centauri), awaiting discovery in existing telescope data. This makes the search for new brown dwarfs very exciting!

# Motions of stars

Brown dwarfs are cold and dim, so they can only be detected when nearby to us. All inhabitants of our Milky Way Galaxy, such as stars and brown dwarfs, are moving relative to the Sun. But we perceive the objects close to us as having a high apparent motion across the sky. This can be seen in the Barnard's Star example image blink from today's lecture.

<center><img src="https://upload.wikimedia.org/wikipedia/commons/6/6c/Barnard2005.gif" width="400"></center>

Mathematically, for a star of fixed speed $v$ (in the plane perpendicular to the line of sight from us to the star), we have:

$\mu \propto v/d$

Here $v$ would be in units of distance over time (like m/s or km/s), $d$ is the distance between us and the star (in units like light years) and $\mu$ is the rate of apparent motion across the sky, which astronomers refer to as **proper motion**. Proper motion has units of angular displacement per unit time. It turns out that the convenient unit of proper motion for nearby stars is arcseconds per year, where one arcsecond is 1/3600 of a degree. Barnard's Star has the highest proper motion of any currently known star or brown dwarf at, roughly 10.4 arcseconds/year. It is possible that through searches like Backyard Worlds, we could discover a brown dwarf that breaks this proper motion record!

Let's take a look at how the fast apparent motion of Barnard's Star plays out in a modern astronomical catalog (from the [Gaia](https://en.wikipedia.org/wiki/Gaia_(spacecraft)) mission). The code below shows a 20 arcminute by 20 arcminute patch of the sky, similar is similar in size to the full Moon.



In [1]:
# set up Python environment...

from ipywidgets import *
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

**Bonus Discussion Question**: after a long time, all the stars in this visualization "go away". If we were to actually look at a patch of sky for millions of years, would all the stars "go away"?

# Colors of stars and brown dwarfs

If you've looked at the night sky, you've probably noticed that stars come in different colors. The color of a star is indicative of its temperature. A blue/white looking star is relatively hot, while a red star (say, a red dwarf like Barnard's Star) will look more yellow/orange in color.

In terms of physics, this is because the peak wavelength of

...equation...

The following code makes plots illustrating how the color of a star shifts from blue to red as you go from the hottest stars ($\sim$50,000 Kelvin) to the coldest known brown dwarfs ($\sim$250 Kelvin).


The left hand plot shows how the spectrum and peak wavelength shift from blue to red as you go from a hotter to a colder star (assuming simplified blackbody emission for now). The right hand plot shows the ratio of amount of light in two infrared wavelength windows, one centered at $\sim$3.5 microns and the other centered at $\sim$4.5 microns. Most stars have a fairly similar ratio of light at 4.5 microns to light at 3.5 microns. But when we reach the coldest brown dwarfs, this ratio becomes dramatically higher. Thus, we can search for cold nearby brown dwarfs not only based on their proper motion, but also based on their color at infrared wavelengths. Objects that look very bright at 4.5 microns relative to how bright they are at 3.5 microns will be strong brown dwarf candidates. 

In [5]:
url = 'https://raw.githubusercontent.com/ameisner/cafe/master/etc/blackbody_wise_flux_ratios.csv'
df = pd.read_csv(url)

def plot_planck(T):
  # make sure to normalize

  plt.figure(figsize=(18, 4))
  plt.subplot(1, 2, 1)
  lambda_values_nm = np.arange(100, 8000)
  lambda_values_m = (1e-9)*lambda_values_nm

  c = 3e8
  nu_values = c/lambda_values_m

  k_b = 1.380649e-23
  h = 6.62607015e-34

  B_nu_T = np.power(nu_values, 3)/(np.exp(h*nu_values/(k_b*T)) - 1)

  B_nu_T /= np.max(B_nu_T) # normalize so that the peak has value 1

  lambda_values_um = lambda_values_nm/1000
  plt.plot(lambda_values_um, B_nu_T, c='k')

  wav_lim_um_blue = (3, 3.9)
  wav_lim_um_red = (4.1, 5)

  plt.plot([3,3], [0, 1], c='b')
  plt.plot([3.9,3.9], [0, 1], c='b')
  plt.plot([4.1,4.1], [0, 1], c='r')
  plt.plot([5, 5], [0, 1], c='r')


  plt.ylim((0, 1))
  plt.xlim((0, 8))

  plt.title('temperature = ' + str(int(T)) + ' Kelvin')
  plt.xlabel('wavelength (microns)')
  plt.ylabel('normalized flux per unit frequency')

  plt.subplot(1, 2, 2)

  flux_ratio_num = np.sum(B_nu_T[(lambda_values_um > wav_lim_um_red[0]) & (lambda_values_um < wav_lim_um_red[1])]) 
  flux_ratio_den = np.sum(B_nu_T[(lambda_values_um > wav_lim_um_blue[0]) & (lambda_values_um < wav_lim_um_blue[1])]) 

  flux_ratio = flux_ratio_num/flux_ratio_den

  global df
  plt.plot(df['t_vals'], df['flux_ratio_vals'], c='k')
  plt.xlim((700, 30000))
  plt.ylim((0, 2))

  plt.scatter([T], [flux_ratio], marker='o', s=100, c='k')

  plt.xlabel('temperature', fontsize=16)
  plt.ylabel('(red flux) / (blue flux) ratio', fontsize=16)

  plt.title('temperature = ' + str(int(T)) + ' Kelvin')

  ax = plt.gca()
  ax.tick_params(axis='both', which='major', labelsize=14)
  ax.tick_params(axis='both', which='minor', labelsize=14)


layout = {'width':'initial'}
box_layout = {'display':'flex', 'flex_flow':'column', 'align-items':'center', 'border':'1px solid grey', 'width':'initial'}

T = FloatSlider(value=5000, min=700, max=30000, step=50, continuous_update=True, layout=layout)

plot4 = interactive(plot_planck, T=T)
plot4.layout = box_layout
display(plot4)

interactive(children=(FloatSlider(value=5000.0, description='T', layout=Layout(width='initial'), max=30000.0, …

**Bonus Physics Question**: you'll notice that for most temperatures in the right hand plot, the ratio of flux at 3 microns to flux at 4 microns is relatively constant. Why is that?

Incidentally, the detailed spectra of brown dwarfs look much weirder than a simple blackbody, primarily due to methane and water absorption that carve out deep valleys and sharp peaks in the profile of light as a function of wavelength. An example is shown below:

<img src="https://astrobites.org/wp-content/uploads/2017/05/fig2.png" width="800">

The temperature of [this object](https://en.wikipedia.org/wiki/WISEA_1101%2B5400) (the first brown dwarf discovered by Backyard Worlds citizen scientists!) is $\sim$1200 Kelvin. For comparison, the Sun's temperature is a much hotter $\sim$5,800 Kelvin and Jupiter's temperature is significant cooler, $\sim$150 Kelvin.

# Looking for brown dwarfs based on motion & color

Now that we have some background on the distinctive motions and colors of brown dwarfs, let's discuss how Backyard Worlds uses both of these traits to discover new brown dwarfs nearby to the Sun. Backyard Worlds looks at images from NASA's [Wide-field Infrared Survey Explorer](https://en.wikipedia.org/wiki/Wide-field_Infrared_Survey_Explorer) (WISE) telescope. These images have square pixels that are 2.75 arcseconds on a side, and span a $\sim$10 year time period (from roughly 2010 to 2020). So Barnard's Star would appear to move by

10 arcseconds/year $\times$ 10 years / (2.75 arcseconds/pixel) $\sim$ 38 WISE pixels

Over the course of the available data.

What is the limit of motions we can detected with the WISE data? Roughly speaking, we can 'see' a movement of about 1 pixel, which would correspond to:

2.75 arcseconds / 10 years = 0.275 arcseoncds per year.

Let's visually examine a few examples of what recent brown dwarf discoveries made by Backyard Worlds citizen scientists look like in the actual WISE data used to discover them. Here's what a brown dwarf moving at roughly 1 arcsecond per year looks like.

This brown dwarf was first discovered by Backyard Worlds citizen scientists Dan Caselden and Melina Thevenot, in 2018. Notice that in addition to the motion of this object, it has a distinctive orange color very different from the black color of much more distant stars and galaxies in the image.

Here's a brown dwarf moving significantly slower ($\sim$0.25 arcseconds/year, roughly 40$\times$ slower than Barnard's star), but still in a way that's visually perceptible relative to the much more distant background stars and galaxies that appear to stay fixed.

This brown dwarf was first discovered by Backyard Worlds citizen scientists XX in 2019.

Here's a trickier case. In the initial part of the animation, the brown dwarf overlaps with a brighter star. Astronomers call this "blending" or "source confusion". This blending often fools computer-based searches for brown dwarfs, because it messes up the automated color and motion measurements. But luckily citizen scientists searching visually can understand what's going on!

Let's keep going on the theme of tricky cases. In addition to blending/confusion, detector noise and defects can also masquerade as red and/or moving sources, and therefore show up as "bogus" brown dwarf candidates. Here's one example, a so-called "ghost" in the WISE data:

It looks very red, but it has an odd donut-shaped appearance which is different from the shape of stars in the imagery, hence we know it can't be a real brown dwarf.

Here's another bogus candidate, this time a piece of a bright star's [diffraction spike](https://en.wikipedia.org/wiki/Diffraction_spike):



Lastly, "crowded fields" -- areas of the sky such as the plane of our Milky Way Galaxy with lots of stars -- can be more difficult to comprehend, both for computer programs and for humans. Here's a crowded field example:


# Discover the brown dwarfs!

Here's a Google Sheet with 30 brown dwarf candidates. The candidate in each case is the object at the center of the image. Each team should collaborate on its own copy of the spreadsheet, filling out the "NOTES" column with the team members' thoughts about whether each candidate is a brown dwarf or not. Then we will reconvene the whole group to discuss! By the way, all of the brown dwarfs in this example data set were first discovered by Backyard Worlds volunteers within the last few years!

# Like staring at movies of brown dwarf candidates?

Anyone can participate in the Backyard Worlds project, which is accessible online for free and with no registration required at:

https://backyardworlds.org/